#Imports

In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import plotly.express as px
import statistics
from plotly.subplots import make_subplots
from scipy.stats import skew
from scipy.stats import kurtosis
import warnings
warnings.filterwarnings('ignore')

#Data

In [ ]:
df = pd.read_json('/content/bitcoin_binance_trade_11.json')
df = df.iloc[:int(0.96*len(df))]
df

time         id  ...     price       qty
0       2021-03-16T00:00:00.056000Z  708932808  ...  55605.20  0.060252
1       2021-03-16T00:00:00.070000Z  708932809  ...  55605.20  0.003996
2       2021-03-16T00:00:00.070000Z  708932810  ...  55605.21  0.000359
3       2021-03-16T00:00:00.076000Z  708932811  ...  55605.20  0.194010
4       2021-03-16T00:00:00.085000Z  708932812  ...  55605.20  0.067000
...                             ...        ...  ...       ...       ...
936123  2021-03-16T10:02:51.957000Z  709961236  ...  56051.06  0.011328
936124  2021-03-16T10:02:52.153000Z  709961237  ...  56051.07  0.001680
936125  2021-03-16T10:02:52.164000Z  709961238  ...  56051.07  0.001680
936126  2021-03-16T10:02:52.192000Z  709961239  ...  56051.08  0.002138
936127  2021-03-16T10:02:52.195000Z  709961240  ...  56051.07  0.007821

[936128 rows x 6 columns]

In [ ]:
import pandas as pd
import time
s = time.time()
df = pd.read_csv("/content/test.csv")
e = time.time()
print("Pandas Loading Time = {}".format(e-s))


Pandas Loading Time = 1.2071750164031982


In [ ]:

import modin.pandas as pdd
s = time.time()
df = pdd.read_csv("/content/test.csv")
e = time.time()
print("Modin Loading Time = {}".format(e-s))

Modin Loading Time = 1.2562074661254883


In [ ]:
px.line(df.iloc[int(0.8*len(df)):],x = 'time', y = 'price')

In [ ]:
df_ = df.iloc[:int(0.24*len(df)),:]
df_

time         id  ...     price       qty
0       2021-03-16T00:00:00.056000Z  708932808  ...  55605.20  0.060252
1       2021-03-16T00:00:00.070000Z  708932809  ...  55605.20  0.003996
2       2021-03-16T00:00:00.070000Z  708932810  ...  55605.21  0.000359
3       2021-03-16T00:00:00.076000Z  708932811  ...  55605.20  0.194010
4       2021-03-16T00:00:00.085000Z  708932812  ...  55605.20  0.067000
...                             ...        ...  ...       ...       ...
224665  2021-03-16T01:19:20.020000Z  709204574  ...  53876.93  0.001226
224666  2021-03-16T01:19:20.022000Z  709204575  ...  53876.94  0.001881
224667  2021-03-16T01:19:20.091000Z  709204576  ...  53876.93  0.000919
224668  2021-03-16T01:19:20.092000Z  709204577  ...  53876.94  0.000453
224669  2021-03-16T01:19:20.227000Z  709204578  ...  53876.94  0.014860

[224670 rows x 6 columns]

#Candle And Its Features - Code

In [ ]:
class candle:

  def candle_and_features(self, memory, imbalanced_or_runs = False, theta_T = None):

    high = np.max(memory['price'])
    low =  np.min(memory['price'])
    close = memory['price'].values[-1]
    open = memory['price'].values[0]
    volume = np.sum(memory['qty'])
    time = memory['time'].values[0]
    mean_price = np.mean(memory['price'])
    mean_volume = np.mean(memory['qty'])
    #mod_price = statistics.mode(memory['price'])[0]
    #mod_volume = statistics.mode(memory['qty'])[0]
    median_price = statistics.median(memory['price'])
    median_volume = statistics.median(memory['qty'])
    std_price = np.std(memory['price'])
    std_volume = np.std(memory['qty'])
    upper_band_price = mean_price + 2*std_price
    lower_band_price = mean_price - 2*std_price
    upper_band_volume = mean_volume + 2*std_volume
    lower_band_volume = mean_volume - 2*std_volume
    skewness_price = skew(memory['price'], bias=False)
    kurtos_price = kurtosis(memory['price'], bias=False)
    skewness_volume = skew(memory['qty'], bias=False)
    kurtos_volume = kurtosis(memory['qty'], bias=False)
    vwap = np.average(memory['price'], weights=memory['qty'])
    no_ticks = len(memory)

    if imbalanced_or_runs:

      theta_is_positive = 1 if theta_T>=0 else 0
      close_gre_open = 1 if close>=open else 0
      new_row = np.array([time,open,high,low,close,volume,vwap,
                                mean_price,#mod_price,
                                median_price,std_price,skewness_price,kurtos_price,lower_band_price,upper_band_price,
                                mean_volume,#mod_volume,
                                median_volume,std_volume,skewness_volume,kurtos_volume,lower_band_volume,upper_band_volume,no_ticks,theta_is_positive,close_gre_open])
      cols = ['time','open','high','low','close','volume','vwap',
                            'mean_price',#'mod_price',
                            'median_price','std_price','skewness_price','kurtos_price','lower_band_price','upper_band_price',
                            'mean_volume',#'mod_volume',
                            'median_volume','std_volume','skewness_volume','kurtos_volume','lower_band_volume','upper_band_volume',
                            '#ticks','theta_is_positive?','candle_is_green?'
                            ]
    else:

      new_row = np.array([time,open,high,low,close,volume,vwap,
                                  mean_price,#mod_price,
                                  median_price,std_price,skewness_price,kurtos_price,lower_band_price,upper_band_price,
                                  mean_volume,#mod_volume,
                                  median_volume,std_volume,skewness_volume,kurtos_volume,lower_band_volume,upper_band_volume,no_ticks])
      cols = ['time','open','high','low','close','volume','vwap',
                                  'mean_price',#'mod_price',
                                  'median_price','std_price','skewness_price','kurtos_price','lower_band_price','upper_band_price',
                                  'mean_volume',#'mod_volume',
                                  'median_volume','std_volume','skewness_volume','kurtos_volume','lower_band_volume','upper_band_volume','#ticks'
                                  ]
    
    return (new_row, cols)


#Time Bars - Code

In [ ]:
class time_bars(candle):

  def __init__(self, df):

    self.df = df
    self.df_time_bar = pd.DataFrame(None)

  def time_bar_chart(self,timestamp='5m'):

    self.df_time_bar = self.df.resample(timestamp).agg({'price': 'ohlc', 'qty': 'sum'})

    return self.df_time_bar


#Balanced Charts - Code

In [ ]:
class balanced_charts(candle):

  def __init__(self, df):

    self.df = df
    self.df_tick = pd.DataFrame(None)
    self.df_volume = pd.DataFrame(None)
    self.df_dollar = pd.DataFrame(None)


  def tick_bar(self, number_of_tick_data):

    self.number_of_tick_data = number_of_tick_data

    number_of_candles = int(len(self.df)/self.number_of_tick_data) + 1

    for i in range(number_of_candles):

      if i==number_of_candles-1:

        candle = self.df.iloc[i*self.number_of_tick_data:,:]
      else:

        candle = self.df.iloc[i*self.number_of_tick_data:(i+1)*self.number_of_tick_data,:]
      values, columns = self.candle_and_features(candle)
      self.df_tick = self.df_tick.append([values])

    self.df_tick.index = np.array(range(len(self.df_tick)))
    self.df_tick.columns = columns

    self.df_tick[self.df_tick.columns[1:]] = self.df_tick[self.df_tick.columns[1:]].apply(pd.to_numeric)
    for u in range(len(self.df_tick)):

      self.df_tick['time'][u] = pd.to_datetime(self.df_tick['time'][u].replace('T',' ').replace('Z','').split('.')[0])

    return self.df_tick

  def volume_bar(self, threshold_for_volume):

    sum = 0
    j = 0
    k = 0

    while j<len(self.df):

      sum += self.df['qty'][j]
      memory = self.df.iloc[k:j+1,:]

      if sum >= threshold_for_volume:


        values, columns = self.candle_and_features(memory)
        self.df_volume = self.df_volume.append([values])

        k = j + 1
        sum = 0
      
      j += 1

    self.df_volume.index = np.array(range(len(self.df_volume)))
    self.df_volume.columns = columns

    self.df_volume[self.df_volume.columns[1:]] = self.df_volume[self.df_volume.columns[1:]].apply(pd.to_numeric)
    for u in range(len(self.df_volume)):

      self.df_volume['time'][u] = pd.to_datetime(self.df_volume['time'][u].replace('T',' ').replace('Z','').split('.')[0])

    return self.df_volume

  def dollar_bar(self, threshold_for_dollar):

    sum = 0
    j = 0
    k = 0

    while j<len(self.df):

      sum += self.df['qty'][j] * self.df['price'][j]
      memory = self.df.iloc[k:j+1,:]
      if sum >= threshold_for_dollar:
        values, columns = self.candle_and_features(memory)
        self.df_dollar = self.df_dollar.append([values])

        k = j + 1
        sum = 0
      
      j += 1

    self.df_dollar.index = np.array(range(len(self.df_dollar)))
    self.df_dollar.columns = columns

    self.df_dollar[self.df_dollar.columns[1:]] = self.df_dollar[self.df_dollar.columns[1:]].apply(pd.to_numeric)
    for u in range(len(self.df_dollar)):

      self.df_dollar['time'][u] = pd.to_datetime(self.df_dollar['time'][u].replace('T',' ').replace('Z','').split('.')[0])

    return self.df_dollar

#Imbalanced Charts - Code

In [ ]:
class imbalanced_charts(candle):

  def __init__(self, df):

    self.df = df
    self.df_tick = pd.DataFrame(None)
    self.df_volume = pd.DataFrame(None)
    self.df_dollar = pd.DataFrame(None)


  def ema(self, s, n):

    s = np.array(s)
    ema = []
    j = 1

    #get n sma first and calculate the next n period ema
    sma = sum(s[:n]) / n
    multiplier = 0.9
    ema.append(sma)

    #EMA(current) = ( (Price(current) - EMA(prev) ) x Multiplier) + EMA(prev)
    ema.append(( (s[n] - sma) * multiplier) + sma)

    #now calculate the rest of the values
    for i in s[n+1:]:
        tmp = ( (i - ema[j]) * multiplier) + ema[j]
        j = j + 1
        ema.append(tmp)

    return ema[-1]



  def tick_bar(self, initial_value = 5000):
    
    theta_T = 0
    j, o = initial_value, initial_value
    b_previous = 1
    counter = 0
    last_tick = False
    candles_with_label_one = 0
    ticks = [j]
    initial_prob = []
    E_0_T = j

    for i in range(1,j):

      change = self.df['price'][self.df.index[i]] - self.df['price'][self.df.index[i-1]] 

      if change > 0:

        initial_prob.append(1.0)
        b_previous = 1
        
      elif change < 0:

        initial_prob.append(0.0)

        b_previous = -1

      else:

        if b_previous == 1.0:
          initial_prob.append(1.0)
        else:
          initial_prob.append(0.0)

    
    prob_1 = sum(initial_prob)/j
    probs = [prob_1]


    while j < len(self.df):

      counter += 1

      if j == len(self.df) - 1:

        last_tick = True

      memory = self.df.iloc[o:j+1,:]

      change = self.df['price'][self.df.index[j]] - self.df['price'][self.df.index[j-1]] 
      
      if change > 0:

        candles_with_label_one += 1
        b_t, b_previous = 1,1
        
      elif change < 0:

        b_t, b_previous = -1,-1

      else:

        b_t = b_previous

        if b_t > 0:
          candles_with_label_one += 1

      theta_T += b_t

      dif = 2*prob_1 - 1
        
      E_0_theta_T = E_0_T * dif

      if abs(theta_T) > abs(E_0_theta_T) or last_tick:

        ticks.append(len(memory))
        E_0_T = self.ema(ticks, len(ticks)-1)
        ratio = candles_with_label_one/counter
        probs.append(ratio)
        prob_1 = self.ema(probs, len(probs)-1)
        values, columns = self.candle_and_features(memory, True, theta_T)
        self.df_tick = self.df_tick.append([values])

        o = j + 1
        counter, candles_with_label_one, theta_T = 0, 0, 0


        if last_tick:

          break

      j += 1

    self.df_tick.index = np.array(range(len(self.df_tick)))
    self.df_tick.columns = columns

    self.df_tick[self.df_tick.columns[1:]] = self.df_tick[self.df_tick.columns[1:]].apply(pd.to_numeric)
    for u in range(len(self.df_tick)):

      self.df_tick['time'][u] = pd.to_datetime(self.df_tick['time'][u].replace('T',' ').replace('Z','').split('.')[0])
    

    return self.df_tick


  def volume_bar(self, initial_values = 10000):
    
    theta_T = 0
    j, o = initial_value, initial_value
    b_previous = 1
    counter = 0
    last_tick = False
    candles_with_label_one, candles_with_label_none = 0, 0
    ticks = [j]
    initial_prob = []
    E_0_T = j
    V_B_1_hist, sum_v_b_1 = [], 0
    V_B_NEG_1_hist, sum_v_b_negative_1 = [], 0
    v_c_c_1, v_c_c_negative_1 = 0, 0
    c_aux_1 = 0
    c_aux_negative_1 = 0

    for i in range(1,j):

      change = self.df['price'][self.df.index[i]] - self.df['price'][self.df.index[i-1]] 

      if change > 0:
       
        sum_v_b_1 += self.df['qty'][self.df.index[i]]
        c_aux_1 += 1
        initial_prob.append(1.0)
        b_previous = 1
        
      elif change < 0:

        sum_v_b_negative_1 += self.df['qty'][self.df.index[i]]
        c_aux_negative_1 += 1 
        initial_prob.append(0.0)
        b_previous = -1

      else:

        if b_previous == 1.0:

          sum_v_b_1 += self.df['qty'][self.df.index[i]]
          c_aux_1 +=1 
          initial_prob.append(1.0)

        else:

          sum_v_b_negative_1 += self.df['qty'][self.df.index[i]]
          c_aux_negative_1 += 1 
          initial_prob.append(0.0)

    V_B_1_hist.append(sum_v_b_1/c_aux_1)
    V_B_NEG_1_hist.append(sum_v_b_negative_1/c_aux_negative_1)

    E_V_b_1 = sum_v_b_1 / c_aux_1
    E_V_b_negative_1 = sum_v_b_negative_1 / c_aux_negative_1

    prob_1 = sum(initial_prob)/j
    probs = [prob_1]

    while j < len(self.df):

      counter += 1

      if j == len(self.df) - 1:

        last_tick = True

      memory = self.df.iloc[o:j+1,:]

      change = self.df['price'][self.df.index[j]] - self.df['price'][self.df.index[j-1]] 
      v_t = self.df['qty'][self.df.index[j]]
      
      if change > 0:

        v_c_c_1 += v_t
        candles_with_label_one += 1
        b_t, b_previous = 1,1
        
      elif change < 0:

        v_c_c_negative_1 += v_t
        candles_with_label_none += 1
        b_t, b_previous = -1,-1

      else:

        b_t = b_previous

        if b_t > 0:
          v_c_c_1 += v_t
          candles_with_label_one += 1
        else:
          v_c_c_negative_1 += v_t
          candles_with_label_none += 1

      theta_T += b_t * v_t

      
        
      E_0_theta_T = E_0_T * (prob_1 * E_V_b_1 - (1-prob_1) * E_V_b_negative_1)
      

      if abs(theta_T) > abs(E_0_theta_T) or last_tick:

        ticks.append(len(memory))
        E_0_T = self.ema(ticks, len(ticks)-1)
        

        V_B_1_hist.append(v_c_c_1/(candles_with_label_one+1))
        V_B_NEG_1_hist.append(v_c_c_negative_1/(candles_with_label_none+1))

        E_V_b_1 = self.ema(V_B_1_hist, len(V_B_1_hist)-1)
        E_V_b_negative_1 = self.ema(V_B_NEG_1_hist, len(V_B_NEG_1_hist)-1)

        ratio = candles_with_label_one/counter
        probs.append(ratio)
        prob_1 = self.ema(probs, len(probs)-1)
        values, columns = self.candle_and_features(memory, True, theta_T)
        self.df_volume = self.df_volume.append([values])

        o = j + 1
        counter, candles_with_label_one, theta_T, v_c_c_1, v_c_c_negative_1 ,candles_with_label_none = 0, 0, 0, 0, 0, 0


        if last_tick:

          break

      j += 1

    self.df_volume.index = np.array(range(len(self.df_volume)))
    self.df_volume.columns = columns


    self.df_volume[self.df_volume.columns[1:]] = self.df_volume[self.df_volume.columns[1:]].apply(pd.to_numeric)
    for u in range(len(self.df_volume)):

      self.df_volume['time'][u] = pd.to_datetime(self.df_volume['time'][u].replace('T',' ').replace('Z','').split('.')[0])
    return self.df_volume


  def dollar_bar(self, initial_value = 10000):
    
    theta_T = 0
    j, o = initial_value, initial_value

    b_previous = 1
    counter = 0
    last_tick = False
    candles_with_label_one, candles_with_label_none = 0, 0
    ticks = [j]
    initial_prob = []
    E_0_T = j
    D_B_1_hist, sum_d_b_1 = [], 0
    D_B_negative_1_hist, sum_d_b_negative_1 = [], 0
    d_c_c_1, d_c_c_negative_1 = 0, 0
    c_aux_1 = 0
    c_aux_negative_1 = 0

    for i in range(1,j):

      change = self.df['price'][self.df.index[i]] - self.df['price'][self.df.index[i-1]] 

      if change > 0:
       
        sum_d_b_1 += self.df['qty'][self.df.index[i]] *  self.df['price'][self.df.index[i]] 
        c_aux_1 += 1
        initial_prob.append(1.0)
        b_previous = 1
        
      elif change < 0:

        sum_d_b_negative_1 += self.df['qty'][self.df.index[i]] * self.df['price'][self.df.index[i]]
        c_aux_negative_1 += 1 
        initial_prob.append(0.0)
        b_previous = -1

      else:

        if b_previous == 1.0:

          sum_d_b_1 += self.df['qty'][self.df.index[i]] *  self.df['price'][self.df.index[i]]
          c_aux_1 +=1 
          initial_prob.append(1.0)

        else:

          sum_d_b_negative_1 += self.df['qty'][self.df.index[i]] *  self.df['price'][self.df.index[i]]
          c_aux_negative_1 += 1 
          initial_prob.append(0.0)

    D_B_1_hist.append(sum_d_b_1/c_aux_1)
    D_B_negative_1_hist.append(sum_d_b_negative_1/c_aux_negative_1)

    E_D_b_1 = sum_d_b_1 / c_aux_1
    E_D_b_negative_1 = sum_d_b_negative_1 / c_aux_negative_1

    prob_1 = sum(initial_prob)/j
    probs = [prob_1]

    while j < len(self.df):

      counter += 1

      if j == len(self.df) - 1:

        last_tick = True

      memory = self.df.iloc[o:j+1,:]

      change = self.df['price'][self.df.index[j]] - self.df['price'][self.df.index[j-1]] 
      d_t = self.df['qty'][self.df.index[j]] * self.df['price'][self.df.index[j]]
      
      if change > 0:

        d_c_c_1 += d_t
        candles_with_label_one += 1
        b_t, b_previous = 1,1
        
      elif change < 0:

        d_c_c_negative_1 += d_t
        candles_with_label_none += 1
        b_t, b_previous = -1,-1

      else:

        b_t = b_previous

        if b_t > 0:
          d_c_c_1 += d_t
          candles_with_label_one += 1
        else:
          d_c_c_negative_1 += d_t
          candles_with_label_none += 1

      theta_T += b_t * d_t

      
        
      E_0_theta_T = E_0_T * (prob_1 * E_D_b_1 - (1-prob_1) * E_D_b_negative_1)
      

      if abs(theta_T) > abs(E_0_theta_T) or last_tick:

        ticks.append(len(memory))
        E_0_T = self.ema(ticks, len(ticks)-1)
        

        D_B_1_hist.append(d_c_c_1/(candles_with_label_one+1))
        D_B_negative_1_hist.append(d_c_c_negative_1/(candles_with_label_none+1))

        E_D_b_1 = self.ema(D_B_1_hist, len(D_B_1_hist)-1)
        E_D_b_negative_1 = self.ema(D_B_negative_1_hist, len(D_B_negative_1_hist)-1)

        ratio = candles_with_label_one/counter
        probs.append(ratio)
        prob_1 = self.ema(probs, len(probs)-1)
        values, columns = self.candle_and_features(memory, True, theta_T)
        self.df_dollar = self.df_dollar.append([values])

        o = j + 1
        counter, candles_with_label_one, theta_T, d_c_c_1, d_c_c_negative_1 ,candles_with_label_none = 0, 0, 0, 0, 0, 0


        if last_tick:

          break

      j += 1

    self.df_dollar.index = np.array(range(len(self.df_dollar)))
    self.df_dollar.columns = columns

    self.df_dollar[self.df_dollar.columns[1:]] = self.df_dollar[self.df_dollar.columns[1:]].apply(pd.to_numeric)
    for u in range(len(self.df_dollar)):

      self.df_dollar['time'][u] = pd.to_datetime(self.df_dollar['time'][u].replace('T',' ').replace('Z','').split('.')[0])

    return self.df_dollar

#Run Bars - Code

In [ ]:
class runs_bars(candle):

  def __init__(self, df):

    self.df = df
    self.df_tick = pd.DataFrame(None)
    self.df_volume = pd.DataFrame(None)
    self.df_dollar = pd.DataFrame(None)

  def ema(self, s, n):

    s = np.array(s)
    ema = []
    j = 1

    #get n sma first and calculate the next n period ema
    sma = sum(s[:n]) / n
    multiplier = 0.9
    ema.append(sma)

    #EMA(current) = ( (Price(current) - EMA(prev) ) x Multiplier) + EMA(prev)
    ema.append(( (s[n] - sma) * multiplier) + sma)

    #now calculate the rest of the values
    for i in s[n+1:]:
        tmp = ( (i - ema[j]) * multiplier) + ema[j]
        j = j + 1
        ema.append(tmp)

    return ema[-1]

  def tick_bar(self, initial_value = 5000):
    
    theta_T = 0
    j, o = initial_value, initial_value
    b_previous = 1
    counter = 0
    last_tick = False
    candles_with_label_one, candles_with_label_none = 0, 0
    ticks = [j]
    initial_prob = []
    E_0_T = j

    for i in range(1,j):

      change = self.df['price'][self.df.index[i]] - self.df['price'][self.df.index[i-1]] 

      if change > 0:

        initial_prob.append(1.0)
        b_previous = 1
        
      elif change < 0:

        initial_prob.append(0.0)

        b_previous = -1

      else:

        if b_previous == 1.0:
          initial_prob.append(1.0)
        else:
          initial_prob.append(0.0)

    
    prob_1 = sum(initial_prob)/j
    probs = [prob_1]


    while j < len(self.df):

      counter += 1

      if j == len(self.df) - 1:

        last_tick = True

      memory = self.df.iloc[o:j+1,:]

      change = self.df['price'][self.df.index[j]] - self.df['price'][self.df.index[j-1]] 
      
      if change > 0:

        candles_with_label_one += 1
        b_t, b_previous = 1,1
        
      elif change < 0:

        candles_with_label_none +=1
        b_t, b_previous = -1,-1

      else:

        b_t = b_previous

        if b_t > 0:
          candles_with_label_one += 1
        else:
          candles_with_label_none +=1

      theta_T = max(candles_with_label_one, candles_with_label_none)

      dif = max(prob_1, 1-prob_1)
        
      E_0_theta_T = E_0_T * dif

      if abs(theta_T) > abs(E_0_theta_T) or last_tick:

        ticks.append(len(memory))
        E_0_T = self.ema(ticks, len(ticks)-1)
        ratio = candles_with_label_one/counter
        probs.append(ratio)
        prob_1 = self.ema(probs, len(probs)-1)
        values, columns = self.candle_and_features(memory, True, theta_T)
        self.df_tick = self.df_tick.append([values])

        o = j + 1
        counter, candles_with_label_one, candles_with_label_none, theta_T = 0, 0, 0, 0


        if last_tick:

          break

      j += 1

    self.df_tick.index = np.array(range(len(self.df_tick)))
    self.df_tick.columns = columns

    self.df_tick[self.df_tick.columns[1:]] = self.df_tick[self.df_tick.columns[1:]].apply(pd.to_numeric)
    for u in range(len(self.df_tick)):

      self.df_tick['time'][u] = pd.to_datetime(self.df_tick['time'][u].replace('T',' ').replace('Z','').split('.')[0])

    return self.df_tick

  def volume_bar(self, initial_value=10000):
    
    theta_T = 0
    j, o = initial_value, initial_value

    b_previous = 1
    counter = 0
    last_tick = False
    candles_with_label_one, candles_with_label_none = 0, 0
    ticks = [j]
    initial_prob = []
    E_0_T = j
    V_B_1_hist, sum_v_b_1 = [], 0
    V_B_NEG_1_hist, sum_v_b_negative_1 = [], 0
    v_c_c_1, v_c_c_negative_1 = 0, 0
    c_aux_1 = 0
    c_aux_negative_1 = 0

    for i in range(1,j):

      change = self.df['price'][self.df.index[i]] - self.df['price'][self.df.index[i-1]] 

      if change > 0:
       
        sum_v_b_1 += self.df['qty'][self.df.index[i]]
        c_aux_1 += 1
        initial_prob.append(1.0)
        b_previous = 1
        
      elif change < 0:

        sum_v_b_negative_1 += self.df['qty'][self.df.index[i]]
        c_aux_negative_1 += 1 
        initial_prob.append(0.0)
        b_previous = -1

      else:

        if b_previous == 1.0:

          sum_v_b_1 += self.df['qty'][self.df.index[i]]
          c_aux_1 +=1 
          initial_prob.append(1.0)

        else:

          sum_v_b_negative_1 += self.df['qty'][self.df.index[i]]
          c_aux_negative_1 += 1 
          initial_prob.append(0.0)

    V_B_1_hist.append(sum_v_b_1/c_aux_1)
    V_B_NEG_1_hist.append(sum_v_b_negative_1/c_aux_negative_1)

    E_V_b_1 = sum_v_b_1 / c_aux_1
    E_V_b_negative_1 = sum_v_b_negative_1 / c_aux_negative_1

    prob_1 = sum(initial_prob)/j
    probs = [prob_1]

    while j < len(self.df):

      counter += 1

      if j == len(self.df) - 1:

        last_tick = True

      memory = self.df.iloc[o:j+1,:]

      change = self.df['price'][self.df.index[j]] - self.df['price'][self.df.index[j-1]] 
      v_t = self.df['qty'][self.df.index[j]]
      
      if change > 0:

        v_c_c_1 += v_t
        candles_with_label_one += 1
        b_t, b_previous = 1,1
        
      elif change < 0:

        v_c_c_negative_1 += v_t
        candles_with_label_none += 1
        b_t, b_previous = -1,-1

      else:

        b_t = b_previous

        if b_t > 0:
          v_c_c_1 += v_t
          candles_with_label_one += 1
        else:
          v_c_c_negative_1 += v_t
          candles_with_label_none += 1

      theta_T = max(v_c_c_1, v_c_c_negative_1)

      
        
      E_0_theta_T = E_0_T * (max(prob_1 * E_V_b_1 , (1-prob_1) * E_V_b_negative_1))
      

      if abs(theta_T) > abs(E_0_theta_T) or last_tick:

        ticks.append(len(memory))
        E_0_T = self.ema(ticks, len(ticks)-1)
        

        V_B_1_hist.append(v_c_c_1/(candles_with_label_one+1))
        V_B_NEG_1_hist.append(v_c_c_negative_1/(candles_with_label_none+1))

        E_V_b_1 = self.ema(V_B_1_hist, len(V_B_1_hist)-1)
        E_V_b_negative_1 = self.ema(V_B_NEG_1_hist, len(V_B_NEG_1_hist)-1)

        ratio = candles_with_label_one/counter
        probs.append(ratio)
        prob_1 = self.ema(probs, len(probs)-1)
        values, columns = self.candle_and_features(memory, True, theta_T)
        self.df_volume = self.df_volume.append([values])

        o = j + 1
        counter, candles_with_label_one, theta_T, v_c_c_1, v_c_c_negative_1 ,candles_with_label_none = 0, 0, 0, 0, 0, 0


        if last_tick:

          break

      j += 1

    self.df_volume.index = np.array(range(len(self.df_volume)))
    self.df_volume.columns = columns


    self.df_volume[self.df_volume.columns[1:]] = self.df_volume[self.df_volume.columns[1:]].apply(pd.to_numeric)
    for u in range(len(self.df_volume)):

      self.df_volume['time'][u] = pd.to_datetime(self.df_volume['time'][u].replace('T',' ').replace('Z','').split('.')[0])
    return self.df_volume


  def dollar_bar(self,initial_value=10000):
    
    theta_T = 0
    j, o = initial_value, initial_value

    b_previous = 1
    counter = 0
    last_tick = False
    candles_with_label_one, candles_with_label_none = 0, 0
    ticks = [j]
    initial_prob = []
    E_0_T = j
    D_B_1_hist, sum_d_b_1 = [], 0
    D_B_negative_1_hist, sum_d_b_negative_1 = [], 0
    d_c_c_1, d_c_c_negative_1 = 0, 0
    c_aux_1 = 0
    c_aux_negative_1 = 0

    for i in range(1,j):

      change = self.df['price'][self.df.index[i]] - self.df['price'][self.df.index[i-1]] 

      if change > 0:
       
        sum_d_b_1 += self.df['qty'][self.df.index[i]] *  self.df['price'][self.df.index[i]] 
        c_aux_1 += 1
        initial_prob.append(1.0)
        b_previous = 1
        
      elif change < 0:

        sum_d_b_negative_1 += self.df['qty'][self.df.index[i]] * self.df['price'][self.df.index[i]]
        c_aux_negative_1 += 1 
        initial_prob.append(0.0)
        b_previous = -1

      else:

        if b_previous == 1.0:

          sum_d_b_1 += self.df['qty'][self.df.index[i]] *  self.df['price'][self.df.index[i]]
          c_aux_1 +=1 
          initial_prob.append(1.0)

        else:

          sum_d_b_negative_1 += self.df['qty'][self.df.index[i]] *  self.df['price'][self.df.index[i]]
          c_aux_negative_1 += 1 
          initial_prob.append(0.0)

    D_B_1_hist.append(sum_d_b_1/c_aux_1)
    D_B_negative_1_hist.append(sum_d_b_negative_1/c_aux_negative_1)

    E_D_b_1 = sum_d_b_1 / c_aux_1
    E_D_b_negative_1 = sum_d_b_negative_1 / c_aux_negative_1

    prob_1 = sum(initial_prob)/j
    probs = [prob_1]


    while j < len(self.df):

      counter += 1

      if j == len(self.df) - 1:

        last_tick = True

      memory = self.df.iloc[o:j+1,:]

      change = self.df['price'][self.df.index[j]] - self.df['price'][self.df.index[j-1]] 
      d_t = self.df['qty'][self.df.index[j]] * self.df['price'][self.df.index[j]]
      
      if change > 0:

        d_c_c_1 += d_t
        candles_with_label_one += 1
        b_t, b_previous = 1,1
        
      elif change < 0:

        d_c_c_negative_1 += d_t
        candles_with_label_none += 1
        b_t, b_previous = -1,-1

      else:

        b_t = b_previous

        if b_t > 0:
          d_c_c_1 += d_t
          candles_with_label_one += 1
        else:
          d_c_c_negative_1 += d_t
          candles_with_label_none += 1

      theta_T = max(d_c_c_1, d_c_c_negative_1)

      
        
      E_0_theta_T = E_0_T * (max(prob_1 * E_D_b_1 , (1-prob_1) * E_D_b_negative_1))
      

      if abs(theta_T) > abs(E_0_theta_T) or last_tick:

        ticks.append(len(memory))
        E_0_T = self.ema(ticks, len(ticks)-1)
        

        D_B_1_hist.append(d_c_c_1/(candles_with_label_one+1))
        D_B_negative_1_hist.append(d_c_c_negative_1/(candles_with_label_none+1))

        E_D_b_1 = self.ema(D_B_1_hist, len(D_B_1_hist)-1)
        E_D_b_negative_1 = self.ema(D_B_negative_1_hist, len(D_B_negative_1_hist)-1)

        ratio = candles_with_label_one/counter
        probs.append(ratio)
        prob_1 = self.ema(probs, len(probs)-1)
        values, columns = self.candle_and_features(memory, True, theta_T)
        self.df_dollar = self.df_dollar.append([values])

        o = j + 1
        counter, candles_with_label_one, theta_T, d_c_c_1, d_c_c_negative_1 ,candles_with_label_none = 0, 0, 0, 0, 0, 0


        if last_tick:

          break

      j += 1

    self.df_dollar.index = np.array(range(len(self.df_dollar)))
    self.df_dollar.columns = columns

    self.df_dollar[self.df_dollar.columns[1:]] = self.df_dollar[self.df_dollar.columns[1:]].apply(pd.to_numeric)
    for u in range(len(self.df_dollar)):

      self.df_dollar['time'][u] = pd.to_datetime(self.df_dollar['time'][u].replace('T',' ').replace('Z','').split('.')[0])

    return self.df_dollar

#Time Bars - Test

In [ ]:
charts = time_bars(df_)
df_time_bar = charts.time_bar_chart('300s')
df_time_bar

time      open  ...  upper_band_volume  #ticks
0   2021-03-16 00:00:00  55605.20  ...           0.333334   16374
1   2021-03-16 00:05:00  55809.62  ...           0.232185    9827
2   2021-03-16 00:10:00  55963.35  ...           0.259641    7242
3   2021-03-16 00:15:00  55954.39  ...           0.635370    7153
4   2021-03-16 00:20:00  55827.36  ...           0.323025   11685
5   2021-03-16 00:25:00  55175.38  ...           0.517046   18242
6   2021-03-16 00:30:00  54874.09  ...           0.449956   15318
7   2021-03-16 00:35:00  54697.64  ...           0.266992   11005
8   2021-03-16 00:40:00  54806.36  ...           0.333960    9991
9   2021-03-16 00:45:00  54864.01  ...           0.402220   13666
10  2021-03-16 00:50:00  54489.09  ...           0.528101   20824
11  2021-03-16 00:55:00  54113.83  ...           0.548780   11847
12  2021-03-16 01:00:00  54088.77  ...           0.463801   24503
13  2021-03-16 01:05:00  53548.52  ...           0.283356   19058
14  2021-03-16 01:10:00  53732.57  ...           0.321439   14967
15  2021-03-16 01:15:00  53606.07  ...           0.266111   12967

[16 rows x 22 columns]

In [ ]:
fig = make_subplots(rows=1, cols=1)

fig.add_trace( go.Candlestick(x = df_time_bar['time'], close = df_time_bar['close'], high = df_time_bar['high'], low = df_time_bar['low'], open = df_time_bar['open'],name='Candles') , row=1, col=1)
fig.show()

In [ ]:
f = go.FigureWidget()
f.add_scatter(x=df_time_bar['time'],y=df_time_bar['close'],name='close')
f.add_scatter(x=df_time_bar['time'],y=df_time_bar['upper_band_price'],name='upper_band_price')
f.add_scatter(x=df_time_bar['time'],y=df_time_bar['lower_band_price'],name='lower_band_price')

f.show()

##Wanna Save?

In [ ]:
path = 'determine the path here'
df_time_bar.to_csv(path = path)

#Balanced Charts - Test

##Tick

In [ ]:
tick_5_min = 6700
tick_15_min = 20000
tick_30_min = 40000
tick_1_h = 80000
tick_2_h = 160000
tick_4_h = 320000

In [ ]:
charts = balanced_charts(df_)
df_tick_balanced = charts.tick_bar(tick_5_min)
df_tick_balanced

time      open  ...  upper_band_volume  #ticks
0   2021-03-16 00:00:00  55605.20  ...           0.363243    6700
1   2021-03-16 00:01:23  55376.35  ...           0.300005    6700
2   2021-03-16 00:03:59  55487.40  ...           0.296214    6700
3   2021-03-16 00:06:31  56014.40  ...           0.207091    6700
4   2021-03-16 00:10:22  55921.32  ...           0.266387    6700
5   2021-03-16 00:15:01  55955.55  ...           0.509310    6700
6   2021-03-16 00:19:40  55800.00  ...           0.487294    6700
7   2021-03-16 00:23:34  55283.79  ...           0.361218    6700
8   2021-03-16 00:25:15  55320.98  ...           0.649557    6700
9   2021-03-16 00:27:22  55042.17  ...           0.466644    6700
10  2021-03-16 00:28:48  54942.58  ...           0.322383    6700
11  2021-03-16 00:31:12  54912.36  ...           0.475474    6700
12  2021-03-16 00:33:10  54775.20  ...           0.456468    6700
13  2021-03-16 00:35:20  54684.22  ...           0.317250    6700
14  2021-03-16 00:38:18  54844.50  ...           0.256631    6700
15  2021-03-16 00:41:34  54827.32  ...           0.336395    6700
16  2021-03-16 00:45:03  54846.79  ...           0.463768    6700
17  2021-03-16 00:48:10  54459.26  ...           0.335982    6700
18  2021-03-16 00:50:01  54476.68  ...           0.725218    6700
19  2021-03-16 00:51:07  54064.50  ...           0.504032    6700
20  2021-03-16 00:52:24  54165.92  ...           0.269903    6700
21  2021-03-16 00:54:44  54097.69  ...           0.205892    6700
22  2021-03-16 00:57:06  54214.65  ...           0.723391    6700
23  2021-03-16 01:00:13  53931.79  ...           0.491147    6700
24  2021-03-16 01:01:27  53840.50  ...           0.581612    6700
25  2021-03-16 01:03:27  53679.74  ...           0.326066    6700
26  2021-03-16 01:04:29  53429.53  ...           0.332076    6700
27  2021-03-16 01:05:47  53392.45  ...           0.278100    6700
28  2021-03-16 01:07:20  53762.46  ...           0.290542    6700
29  2021-03-16 01:09:09  53510.11  ...           0.259395    6700
30  2021-03-16 01:11:22  53542.98  ...           0.377272    6700
31  2021-03-16 01:13:38  53416.89  ...           0.263359    6700
32  2021-03-16 01:15:52  53719.07  ...           0.254478    6700
33  2021-03-16 01:17:50  54040.28  ...           0.295512    3570

[34 rows x 22 columns]

In [ ]:
fig = make_subplots(rows=1, cols=1)

fig.add_trace( go.Candlestick(x = df_tick_balanced['time'], close = df_tick_balanced['close'], high = df_tick_balanced['high'], low = df_tick_balanced['low'], open = df_tick_balanced['open'],name='Candles') , row=1, col=1)
fig.show()

In [ ]:
f = go.FigureWidget()
f.add_scatter(x=df_tick_balanced['time'],y=df_tick_balanced['close'],name='close')
f.add_scatter(x=df_tick_balanced['time'],y=df_tick_balanced['upper_band_price'],name='upper_band_price')
f.add_scatter(x=df_tick_balanced['time'],y=df_tick_balanced['lower_band_price'],name='lower_band_price')

f.show()

###Wanna Save?

In [ ]:
path = 'determine the path here'
df_tick_balanced.to_csv(path = path)

##Volume

In [ ]:
volume_5_min = 250
volume_15_min = 750
volume_30_min = 1500
volume_1_h = 3000
volume_2_h = 5500
volume_4_h = 10000

In [ ]:
charts = balanced_charts(df_)
df_volume_balanced = charts.volume_bar(volume_5_min)
df_volume_balanced

time      open  ...  upper_band_volume  #ticks
0   2021-03-16 00:00:00  55605.20  ...           0.340364    4799
1   2021-03-16 00:00:51  55359.20  ...           0.351489    5551
2   2021-03-16 00:02:42  55441.49  ...           0.310545    5950
3   2021-03-16 00:04:56  55801.83  ...           0.243652    7558
4   2021-03-16 00:08:24  55871.24  ...           0.228458    7838
5   2021-03-16 00:13:44  55772.82  ...           0.295208    6145
6   2021-03-16 00:17:53  55859.02  ...           0.730672    4819
7   2021-03-16 00:21:32  55687.27  ...           0.292651    5367
8   2021-03-16 00:23:55  55240.80  ...           0.372369    5255
9   2021-03-16 00:25:09  55241.07  ...           0.883858    3221
10  2021-03-16 00:26:03  55084.81  ...           0.403374    5377
11  2021-03-16 00:27:54  55000.00  ...           0.462106    4187
12  2021-03-16 00:28:33  54836.74  ...           0.329398    5799
13  2021-03-16 00:30:27  55087.00  ...           0.292862    5735
14  2021-03-16 00:32:18  54850.36  ...           0.530739    4925
15  2021-03-16 00:34:05  54709.36  ...           0.518939    4204
16  2021-03-16 00:35:10  54713.96  ...           0.329334    5612
17  2021-03-16 00:37:39  54859.97  ...           0.259639    8231
18  2021-03-16 00:41:36  54819.71  ...           0.319263    7614
19  2021-03-16 00:45:41  54822.68  ...           0.503865    5331
20  2021-03-16 00:48:08  54500.00  ...           0.356189    4328
21  2021-03-16 00:49:02  54681.55  ...           0.397038    5537
22  2021-03-16 00:50:24  54278.81  ...           0.783698    4874
23  2021-03-16 00:51:18  54140.04  ...           0.351358    4717
24  2021-03-16 00:52:11  54133.64  ...           0.502604    5275
25  2021-03-16 00:53:46  54300.00  ...           0.220383    7589
26  2021-03-16 00:56:24  54299.70  ...           0.706341    6707
27  2021-03-16 00:59:35  54071.45  ...           0.595909    3926
28  2021-03-16 01:00:35  53795.00  ...           0.703614    4742
29  2021-03-16 01:01:36  53831.80  ...           0.233593    7472
30  2021-03-16 01:03:32  53634.95  ...           0.354580    4671
31  2021-03-16 01:04:18  53485.21  ...           0.353941    5531
32  2021-03-16 01:05:13  53477.35  ...           0.279983    5481
33  2021-03-16 01:06:42  53408.02  ...           0.292774    5464
34  2021-03-16 01:07:53  53800.69  ...           0.268449    6256
35  2021-03-16 01:09:45  53707.77  ...           0.296684    5153
36  2021-03-16 01:11:26  53506.32  ...           0.370854    4760
37  2021-03-16 01:13:01  53298.76  ...           0.288875    5502
38  2021-03-16 01:14:55  53596.25  ...           0.241860    5836
39  2021-03-16 01:16:35  53908.53  ...           0.270446    4885

[40 rows x 22 columns]

In [ ]:
fig = make_subplots(rows=1, cols=1)

fig.add_trace( go.Candlestick(x = df_volume_balanced['time'], close = df_volume_balanced['close'], high = df_volume_balanced['high'], low = df_volume_balanced['low'], open = df_volume_balanced['open'],name='Candles') , row=1, col=1)
fig.show()

In [ ]:
f = go.FigureWidget()
f.add_scatter(x=df_volume_balanced['time'],y=df_volume_balanced['close'],name='close')
f.add_scatter(x=df_volume_balanced['time'],y=df_volume_balanced['upper_band_price'],name='upper_band_price')
f.add_scatter(x=df_volume_balanced['time'],y=df_volume_balanced['lower_band_price'],name='lower_band_price')

f.show()

###Wanna Save?

In [ ]:
path = 'determine the path here'
df_volume_balanced.to_csv(path = path)

##Dollar

In [ ]:
dollar_5_min = 14750000
dollar_15_min = 44250000
dollar_30_min = 88500000
dollar_1_h = 177000000
dollar_2_h = 320000000
dollar_4_h = 640000000

In [ ]:
charts = balanced_charts(df_)
df_dollar_balanced = charts.dollar_bar(dollar_5_min)
df_dollar_balanced

time      open  ...  upper_band_volume  #ticks
0   2021-03-16 00:00:00  55605.20  ...           0.338337    5139
1   2021-03-16 00:00:57  55381.66  ...           0.361094    5712
2   2021-03-16 00:02:56  55424.59  ...           0.287440    7037
3   2021-03-16 00:05:25  55872.40  ...           0.226756    8576
4   2021-03-16 00:10:07  55985.08  ...           0.260445    7754
5   2021-03-16 00:15:24  55892.60  ...           0.348079    5879
6   2021-03-16 00:19:40  55800.00  ...           0.694584    4954
7   2021-03-16 00:22:34  55462.12  ...           0.301506    5849
8   2021-03-16 00:24:36  55109.96  ...           0.842917    3691
9   2021-03-16 00:25:31  55118.86  ...           0.358295    6370
10  2021-03-16 00:27:36  55009.99  ...           0.618623    3203
11  2021-03-16 00:28:04  54950.20  ...           0.313470    6127
12  2021-03-16 00:29:53  54942.59  ...           0.297287    6515
13  2021-03-16 00:32:04  54800.00  ...           0.523691    5177
14  2021-03-16 00:33:55  54800.01  ...           0.485437    4892
15  2021-03-16 00:35:14  54663.94  ...           0.321460    6191
16  2021-03-16 00:38:02  54875.41  ...           0.267293    8981
17  2021-03-16 00:42:25  54715.89  ...           0.368193    7668
18  2021-03-16 00:46:47  54707.97  ...           0.459805    5313
19  2021-03-16 00:48:17  54475.43  ...           0.343184    5353
20  2021-03-16 00:49:56  54537.92  ...           0.835263    4742
21  2021-03-16 00:50:39  54225.60  ...           0.326704    5929
22  2021-03-16 00:51:58  54000.00  ...           0.531882    5071
23  2021-03-16 00:53:02  54231.14  ...           0.249775    7659
24  2021-03-16 00:55:47  54343.44  ...           0.642251    8003
25  2021-03-16 00:59:08  54170.23  ...           0.563094    4565
26  2021-03-16 01:00:35  53800.00  ...           0.705586    4863
27  2021-03-16 01:01:36  53831.80  ...           0.234009    8136
28  2021-03-16 01:03:41  53597.04  ...           0.370590    5055
29  2021-03-16 01:04:30  53400.00  ...           0.321855    6341
30  2021-03-16 01:05:44  53428.87  ...           0.290729    6174
31  2021-03-16 01:07:13  53769.98  ...           0.298640    5942
32  2021-03-16 01:08:45  53510.01  ...           0.237955    6694
33  2021-03-16 01:10:54  53582.74  ...           0.320519    5458
34  2021-03-16 01:12:44  53364.86  ...           0.380542    5247
35  2021-03-16 01:14:35  53468.20  ...           0.234689    6669
36  2021-03-16 01:16:28  53950.00  ...           0.270423    5316

[37 rows x 22 columns]

In [ ]:
fig = make_subplots(rows=1, cols=1)

fig.add_trace( go.Candlestick(x = df_dollar_balanced['time'], close = df_dollar_balanced['close'], high = df_dollar_balanced['high'], low = df_dollar_balanced['low'], open = df_dollar_balanced['open'],name='Candles') , row=1, col=1)
fig.show()

In [ ]:
f = go.FigureWidget()
f.add_scatter(x=df_dollar_balanced['time'],y=df_dollar_balanced['close'],name='close')
f.add_scatter(x=df_dollar_balanced['time'],y=df_dollar_balanced['upper_band_price'],name='upper_band_price')
f.add_scatter(x=df_dollar_balanced['time'],y=df_dollar_balanced['lower_band_price'],name='lower_band_price')

f.show()

###Wanna Save?

In [ ]:
path = 'determine the path here'
df_dollar_balanced.to_csv(path = path)

#Imbalanced Charts - Test

##Tick

In [ ]:
charts = imbalanced_charts(df_)
df_tick_imbalanced = charts.tick_bar()
df_tick_imbalanced

time      open  ...  theta_is_positive?  candle_is_green?
0   2021-03-16 00:00:53  55388.93  ...                   1                 1
1   2021-03-16 00:04:39  55787.08  ...                   1                 1
2   2021-03-16 00:15:01  55955.55  ...                   0                 0
3   2021-03-16 00:15:59  55799.94  ...                   0                 1
4   2021-03-16 00:20:31  55868.35  ...                   0                 0
5   2021-03-16 00:23:05  55512.89  ...                   0                 0
6   2021-03-16 00:24:08  55200.00  ...                   0                 0
7   2021-03-16 00:25:27  55183.33  ...                   0                 0
8   2021-03-16 00:27:31  55004.22  ...                   0                 0
9   2021-03-16 00:27:55  55000.00  ...                   0                 1
10  2021-03-16 00:27:57  55000.00  ...                   0                 0
11  2021-03-16 00:31:29  54771.70  ...                   0                 0
12  2021-03-16 00:47:12  54733.00  ...                   0                 0
13  2021-03-16 00:50:30  54154.25  ...                   0                 0
14  2021-03-16 00:57:15  54144.91  ...                   0                 0
15  2021-03-16 01:04:32  53350.00  ...                   1                 1

[16 rows x 24 columns]

In [ ]:
fig = make_subplots(rows=1, cols=1)

fig.add_trace( go.Candlestick(x = df_tick_imbalanced['time'], close = df_tick_imbalanced['close'], high = df_tick_imbalanced['high'], low = df_tick_imbalanced['low'], open = df_tick_imbalanced['open'],name='Candles') , row=1, col=1)
fig.show()

In [ ]:
f = go.FigureWidget()
f.add_scatter(x=df_tick_imbalanced['time'],y=df_tick_imbalanced['close'],name='close')
f.add_scatter(x=df_tick_imbalanced['time'],y=df_tick_imbalanced['upper_band_price'],name='upper_band_price')
f.add_scatter(x=df_tick_imbalanced['time'],y=df_tick_imbalanced['lower_band_price'],name='lower_band_price')


f.show()

###Wanna Save?

In [ ]:
path = 'determine the path here'
df_tick_imbalanced.to_csv(path = path)

##Volume

In [ ]:
charts = imbalanced_charts(df_)
df_volume_imbalanced = charts.volume_bar()
df_volume_imbalanced

time      open  ...  theta_is_positive?  candle_is_green?
0  2021-03-16 00:02:33  55434.75  ...                   1                 1
1  2021-03-16 00:04:26  55699.58  ...                   1                 1
2  2021-03-16 00:06:19  55990.78  ...                   0                 0
3  2021-03-16 00:15:24  55892.60  ...                   0                 0
4  2021-03-16 00:15:58  55872.50  ...                   0                 0
5  2021-03-16 00:19:40  55800.00  ...                   0                 1
6  2021-03-16 00:19:40  55800.00  ...                   0                 0
7  2021-03-16 00:27:50  55000.00  ...                   0                 0
8  2021-03-16 00:51:57  54004.00  ...                   0                 0

[9 rows x 24 columns]

In [ ]:
fig = make_subplots(rows=1, cols=1)

fig.add_trace( go.Candlestick(x = df_volume_imbalanced['time'], close = df_volume_imbalanced['close'], high = df_volume_imbalanced['high'], low = df_volume_imbalanced['low'], open = df_volume_imbalanced['open'],name='Candles') , row=1, col=1)
fig.show()

In [ ]:
f = go.FigureWidget()
f.add_scatter(x=df_volume_imbalanced['time'],y=df_volume_imbalanced['close'],name='close')
f.add_scatter(x=df_volume_imbalanced['time'],y=df_volume_imbalanced['upper_band_price'],name='upper_band_price')
f.add_scatter(x=df_volume_imbalanced['time'],y=df_volume_imbalanced['lower_band_price'],name='lower_band_price')

f.show()

###Wanna Save?

In [ ]:
path = 'determine the path here'
df_volume_imbalanced.to_csv(path = path)

##Dollar

In [ ]:
charts = imbalanced_charts(df_)
df_dollar_imbalanced = charts.dollar_bar()
df_dollar_imbalanced

time      open  ...  theta_is_positive?  candle_is_green?
0  2021-03-16 00:02:33  55434.75  ...                   1                 1
1  2021-03-16 00:04:26  55699.58  ...                   1                 1
2  2021-03-16 00:06:14  55978.70  ...                   0                 0
3  2021-03-16 00:15:24  55892.60  ...                   0                 1
4  2021-03-16 00:15:58  55892.92  ...                   0                 0
5  2021-03-16 00:19:40  55800.00  ...                   0                 1
6  2021-03-16 00:19:40  55800.00  ...                   0                 0
7  2021-03-16 00:27:50  55000.00  ...                   0                 0
8  2021-03-16 00:51:58  54000.00  ...                   1                 0

[9 rows x 24 columns]

In [ ]:
fig = make_subplots(rows=1, cols=1)

fig.add_trace( go.Candlestick(x = df_dollar_imbalanced['time'], close = df_dollar_imbalanced['close'], high = df_dollar_imbalanced['high'], low = df_dollar_imbalanced['low'], open = df_dollar_imbalanced['open'],name='Candles') , row=1, col=1)
fig.show()

In [ ]:
f = go.FigureWidget()
f.add_scatter(x=df_dollar_imbalanced['time'],y=df_dollar_imbalanced['close'],name='close')
f.add_scatter(x=df_dollar_imbalanced['time'],y=df_dollar_imbalanced['upper_band_price'],name='upper_band_price')
f.add_scatter(x=df_dollar_imbalanced['time'],y=df_dollar_imbalanced['lower_band_price'],name='lower_band_price')


f.show()

In [ ]:
(np.sum((df_dollar_imbalanced['close'] - df_volume_imbalanced['close'])**2)/len(df_dollar_imbalanced['close']))**0.5

7.730879639471965

###Wanna Save?

In [ ]:
path = 'determine the path here'
df_dollar_imbalanced.to_csv(path = path)

#Runs Bars - Test

##Tick

In [ ]:
charts = runs_bars(df_)
df_tick_runs = charts.tick_bar()
df_tick_runs

time      open  ...  theta_is_positive?  candle_is_green?
0   2021-03-16 00:00:53  55388.93  ...                   1                 1
1   2021-03-16 00:02:51  55437.54  ...                   1                 1
2   2021-03-16 00:04:38  55798.38  ...                   1                 1
3   2021-03-16 00:07:00  55990.63  ...                   1                 0
4   2021-03-16 00:10:06  55975.86  ...                   1                 0
5   2021-03-16 00:13:55  55773.54  ...                   1                 1
6   2021-03-16 00:17:19  55850.00  ...                   1                 0
7   2021-03-16 00:21:15  55776.95  ...                   1                 0
8   2021-03-16 00:23:38  55298.61  ...                   1                 0
9   2021-03-16 00:24:55  55099.64  ...                   1                 1
10  2021-03-16 00:26:11  55174.25  ...                   1                 0
11  2021-03-16 00:27:54  55000.00  ...                   1                 0
12  2021-03-16 00:28:32  54855.00  ...                   1                 1
13  2021-03-16 00:30:16  55035.38  ...                   1                 0
14  2021-03-16 00:31:52  54739.37  ...                   1                 1
15  2021-03-16 00:33:30  54743.92  ...                   1                 0
16  2021-03-16 00:35:05  54708.99  ...                   1                 1
17  2021-03-16 00:37:12  54805.88  ...                   1                 1
18  2021-03-16 00:39:54  54806.37  ...                   1                 0
19  2021-03-16 00:42:19  54739.96  ...                   1                 1
20  2021-03-16 00:45:02  54847.84  ...                   1                 0
21  2021-03-16 00:47:59  54600.00  ...                   1                 1
22  2021-03-16 00:48:45  54677.94  ...                   1                 0
23  2021-03-16 00:50:13  54300.00  ...                   1                 0
24  2021-03-16 00:51:03  54100.03  ...                   1                 0
25  2021-03-16 00:51:58  54000.00  ...                   1                 1
26  2021-03-16 00:53:07  54260.73  ...                   1                 0
27  2021-03-16 00:55:07  54163.31  ...                   1                 1
28  2021-03-16 00:57:02  54215.04  ...                   1                 0
29  2021-03-16 00:59:30  54101.29  ...                   1                 0
30  2021-03-16 01:00:38  53813.67  ...                   1                 1
31  2021-03-16 01:01:47  53820.26  ...                   1                 0
32  2021-03-16 01:03:25  53701.90  ...                   1                 0
33  2021-03-16 01:04:09  53511.41  ...                   1                 0
34  2021-03-16 01:04:47  53403.97  ...                   1                 0
35  2021-03-16 01:05:59  53355.13  ...                   1                 1
36  2021-03-16 01:07:07  53657.89  ...                   1                 1
37  2021-03-16 01:08:16  53762.84  ...                   1                 0
38  2021-03-16 01:09:44  53697.32  ...                   1                 0
39  2021-03-16 01:11:23  53500.00  ...                   1                 0
40  2021-03-16 01:13:06  53388.13  ...                   1                 1
41  2021-03-16 01:14:49  53600.00  ...                   1                 1
42  2021-03-16 01:16:10  53808.27  ...                   1                 1
43  2021-03-16 01:17:46  54047.40  ...                   1                 0

[44 rows x 24 columns]

In [ ]:
fig = make_subplots(rows=1, cols=1)

fig.add_trace( go.Candlestick(x = df_tick_runs['time'], close = df_tick_runs['close'], high = df_tick_runs['high'], low = df_tick_runs['low'], open = df_tick_runs['open'],name='Candles') , row=1, col=1)
fig.show()

In [ ]:
f = go.FigureWidget()
f.add_scatter(x=df_tick_runs['time'],y=df_tick_runs['close'],name='close')
f.add_scatter(x=df_tick_runs['time'],y=df_tick_runs['upper_band_price'],name='upper_band_price')
f.add_scatter(x=df_tick_runs['time'],y=df_tick_runs['lower_band_price'],name='lower_band_price')


f.show()

###Wanna Save?

In [ ]:
path = 'determine the path here'
df_tick_runs.to_csv(path = path)

##Volume

In [ ]:
charts = runs_bars(df_)
df_volume_runs = charts.volume_bar()
df_volume_runs

time      open  ...  theta_is_positive?  candle_is_green?
0   2021-03-16 00:02:33  55434.75  ...                   1                 1
1   2021-03-16 00:07:38  55953.25  ...                   1                 0
2   2021-03-16 00:16:25  55747.71  ...                   1                 0
3   2021-03-16 00:22:09  55548.05  ...                   1                 0
4   2021-03-16 00:25:14  55314.49  ...                   1                 0
5   2021-03-16 00:27:34  55000.54  ...                   1                 0
6   2021-03-16 00:28:42  54876.39  ...                   1                 0
7   2021-03-16 00:32:34  54733.90  ...                   1                 0
8   2021-03-16 00:35:11  54693.04  ...                   1                 1
9   2021-03-16 00:41:31  54811.84  ...                   1                 0
10  2021-03-16 00:48:05  54513.00  ...                   1                 0
11  2021-03-16 00:50:10  54385.32  ...                   1                 0
12  2021-03-16 00:51:51  54070.38  ...                   1                 1
13  2021-03-16 00:55:01  54123.63  ...                   1                 0
14  2021-03-16 01:00:16  53854.61  ...                   1                 0
15  2021-03-16 01:02:15  53802.02  ...                   1                 0
16  2021-03-16 01:04:29  53424.20  ...                   1                 1
17  2021-03-16 01:06:51  53500.00  ...                   1                 1
18  2021-03-16 01:09:50  53746.05  ...                   1                 0
19  2021-03-16 01:12:59  53328.93  ...                   1                 1
20  2021-03-16 01:16:21  53899.05  ...                   1                 0

[21 rows x 24 columns]

In [ ]:
fig = make_subplots(rows=1, cols=1)

fig.add_trace( go.Candlestick(x = df_volume_runs['time'], close = df_volume_runs['close'], high = df_volume_runs['high'], low = df_volume_runs['low'], open = df_volume_runs['open'],name='Candles') , row=1, col=1)
fig.show()

In [ ]:
f = go.FigureWidget()
f.add_scatter(x=df_volume_runs['time'],y=df_volume_runs['close'],name='close')
f.add_scatter(x=df_volume_runs['time'],y=df_volume_runs['upper_band_price'],name='upper_band_price')
f.add_scatter(x=df_volume_runs['time'],y=df_volume_runs['lower_band_price'],name='lower_band_price')


f.show()

###Wanna Save?

In [ ]:
path = 'determine the path here'
df_volume_runs.to_csv(path = path)

##Dollar

In [ ]:
charts = runs_bars(df_)
df_dollar_runs = charts.dollar_bar()
df_dollar_runs

time      open  ...  theta_is_positive?  candle_is_green?
0   2021-03-16 00:02:33  55434.75  ...                   1                 1
1   2021-03-16 00:07:34  55980.19  ...                   1                 0
2   2021-03-16 00:16:17  55748.16  ...                   1                 0
3   2021-03-16 00:22:06  55513.58  ...                   1                 0
4   2021-03-16 00:25:11  55277.53  ...                   1                 0
5   2021-03-16 00:27:31  55009.00  ...                   1                 0
6   2021-03-16 00:28:42  54902.98  ...                   1                 0
7   2021-03-16 00:32:35  54709.86  ...                   1                 1
8   2021-03-16 00:35:38  54811.30  ...                   1                 0
9   2021-03-16 00:42:31  54752.37  ...                   1                 0
10  2021-03-16 00:48:08  54500.00  ...                   1                 0
11  2021-03-16 00:50:22  54245.03  ...                   1                 0
12  2021-03-16 00:51:58  54000.00  ...                   1                 1
13  2021-03-16 00:55:14  54227.25  ...                   1                 0
14  2021-03-16 01:00:17  53888.00  ...                   1                 0
15  2021-03-16 01:02:19  53772.91  ...                   1                 0
16  2021-03-16 01:04:31  53400.00  ...                   1                 1
17  2021-03-16 01:06:51  53500.00  ...                   1                 1
18  2021-03-16 01:09:59  53725.24  ...                   1                 0
19  2021-03-16 01:13:08  53440.95  ...                   1                 1
20  2021-03-16 01:16:31  53948.18  ...                   1                 0

[21 rows x 24 columns]

In [ ]:
fig = make_subplots(rows=1, cols=1)

fig.add_trace(go.Candlestick(x = df_dollar_runs['time'], close = df_dollar_runs['close'], high = df_dollar_runs['high'], low = df_dollar_runs['low'], open = df_dollar_runs['open'],name='Candles'), row=1, col=1)
fig.show()

In [ ]:
f = go.FigureWidget()
f.add_scatter(x=df_dollar_runs['time'],y=df_dollar_runs['close'],name='close')
f.add_scatter(x=df_dollar_runs['time'],y=df_dollar_runs['upper_band_price'],name='upper_band_price')
f.add_scatter(x=df_dollar_runs['time'],y=df_dollar_runs['lower_band_price'],name='lower_band_price')


f.show()

In [ ]:
(np.sum((df_dollar_runs['close'] - df_volume_runs['close'])**2)/len(df_dollar_runs['close']))**0.5

59.05547295310007

###Wanna Save?

In [ ]:
path = 'determine the path here'
df_dollar_runs.to_csv(path = path)